# 解读 `Span`

## `SpanNode`

```c++

/*!
 * \brief Span information for debugging purposes
 */
class Span;
/*!
 * \brief Stores locations in frontend source that generated a node.
 */
class SpanNode : public Object {
 public:
  /*! \brief The source name. */
  SourceName source_name;
  /*! \brief The line number. */
  int line;
  /*! \brief The column offset. */
  int column;
  /*! \brief The end line number. */
  int end_line;
  /*! \brief The end column number. */
  int end_column;

  // override attr visitor
  void VisitAttrs(AttrVisitor* v) {
    v->Visit("source_name", &source_name);
    v->Visit("line", &line);
    v->Visit("column", &column);
    v->Visit("end_line", &end_line);
    v->Visit("end_column", &end_column);
  }
  static constexpr bool _type_has_method_sequal_reduce = true;

  bool SEqualReduce(const SpanNode* other, SEqualReducer equal) const {
    return equal(source_name, other->source_name) && equal(line, other->line) &&
           equal(column, other->column) && equal(end_line, other->end_line) &&
           equal(end_column, other->end_column);
  }

  static constexpr const char* _type_key = "Span";
  TVM_DECLARE_BASE_OBJECT_INFO(SpanNode, Object);
};
```

`SpanNode` 继承自 `Object` 类的子类，它表示生成节点的前端源代码中的位置信息。该类具有以下成员变量和成员函数：

- `source_name`：`SourceName` 类型的成员变量，表示生成节点的源名称。
- `line`：整数类型的成员变量，表示行号。
- `column`：整数类型的成员变量，表示列偏移量。
- `end_line`：整数类型的成员变量，表示结束行号。
- `end_column`：整数类型的成员变量，表示结束列号。
- `VisitAttrs(AttrVisitor* v)`：成员函数，用于访问属性。它接受指向 `AttrVisitor` 对象的指针作为参数，并依次调用 `v->Visit("source_name", &source_name)`、`v->Visit("line", &line)`、`v->Visit("column", &column)`、`v->Visit("end_line", &end_line)` 和 `v->Visit("end_column", &end_column)` 来访问相应的属性。
- `_type_has_method_sequal_reduce`：静态常量表达式布尔值，表示该类型是否具有 `SEqualReduce` 方法。
- `SEqualReduce(const SpanNode* other, SEqualReducer equal) const`：成员函数，用于比较两个 `SpanNode` 对象是否相等。它接受一个指向另一个 `SpanNode` 对象的指针和一个 `SEqualReducer` 对象作为参数，并使用 `equal` 函数比较两个对象的相应属性是否相等。
- `_type_key`：静态常量字符指针，表示该类型的键。
- `TVM_DECLARE_BASE_OBJECT_INFO(SpanNode, Object)`：宏定义，用于声明 `SpanNode` 对象的基本信息。

总体来说，这段代码定义了表示生成节点位置信息的类，并提供了相应的属性访问和相等性比较功能。

## `Span`

```c++
class Span : public ObjectRef {
 public:
  TVM_DLL Span(SourceName source_name, int line, int end_line, int column, int end_column);

  /*! \brief Merge two spans into one which captures the combined regions. */
  TVM_DLL Span Merge(const Span& other) const;

  TVM_DEFINE_OBJECT_REF_METHODS(Span, ObjectRef, SpanNode);
};
```

`Span` 类继承自 `ObjectRef` 类。该类具有以下成员函数：

- `Span(SourceName source_name, int line, int end_line, int column, int end_column)`：一个构造函数，用于创建 `Span` 对象。它接受五个参数：`source_name` 表示源名称，`line` 表示起始行号， `end_line` 表示结束行号，`column` 表示起始列号，`end_column` 表示结束列号。
- `Merge(const Span& other) const`：成员函数，用于合并两个 `Span` 对象为一个捕获了组合区域的 `Span` 对象。它接受一个指向另一个 `Span` 对象的常量引用作为参数，并返回一个新的 `Span` 对象。
- `TVM_DEFINE_OBJECT_REF_METHODS(Span, ObjectRef, SpanNode)`：宏定义，用于定义 `Span` 对象的引用方法。

总体来说，这段代码定义了一个用于表示源代码片段位置信息的类，并提供了相应的构造函数和合并功能。

## `SequentialSpanNode`

```c++
/*!
 * \brief Store a list of spans for an expr generated from mulitple source exprs
 */
class SequentialSpanNode : public SpanNode {
 public:
  /*! \brief The original source list of spans to construct a sequential span. */
  Array<Span> spans;

  // override attr visitor
  void VisitAttrs(AttrVisitor* v) {
    SpanNode::VisitAttrs(v);
    v->Visit("spans", &spans);
  }

  static constexpr const char* _type_key = "SequentialSpan";
  TVM_DECLARE_FINAL_OBJECT_INFO(SequentialSpanNode, SpanNode);

  bool SEqualReduce(const SequentialSpanNode* other, SEqualReducer equal) const {
    if (spans.size() != other->spans.size()) {
      return false;
    }

    for (size_t i = 0, e = spans.size(); i != e; ++i) {
      if (!StructuralEqual()(spans[i], other->spans[i])) {
        return false;
      }
    }
    return true;
  }
};
```

`SequentialSpanNode` 类继承自 `SpanNode` 类。该类具有以下成员变量和成员函数：

- `spans`：`Array<Span>` 类型的成员变量，表示原始 source exprs 列表中的 span，用于构造顺序 span。
- `VisitAttrs(AttrVisitor* v)`：一个成员函数，用于访问属性。它接受一个指向`AttrVisitor`对象的指针作为参数，并首先调用基类的`VisitAttrs`函数，然后调用`v->Visit("spans", &spans)`来访问`spans`属性。
- `_type_key`：一个静态常量字符指针，表示该类型的键。
- `TVM_DECLARE_FINAL_OBJECT_INFO(SequentialSpanNode, SpanNode)`：一个宏定义，用于声明`SequentialSpanNode`对象的最终信息。
- `SEqualReduce(const SequentialSpanNode* other, SEqualReducer equal) const`：一个成员函数，用于比较两个`SequentialSpanNode`对象是否相等。它接受一个指向另一个`SequentialSpanNode`对象的指针和一个`SEqualReducer`对象作为参数，并使用`equal`函数比较两个对象的`spans`属性是否相等。如果长度不相等或任何一个元素不相等，则返回`false`；否则返回`true`。

总体来说，这段代码定义了一个用于存储由多个源表达式生成的表达式的顺序跨度列表的类，并提供了相应的属性访问和相等性比较功能。

## `SequentialSpan`

```c++
/*!
 * \brief Reference class of SequentialSpanNode.
 * \sa SequentialSpanNode
 */
class SequentialSpan : public Span {
 public:
  TVM_DLL SequentialSpan(Array<Span> spans);

  TVM_DLL SequentialSpan(std::initializer_list<Span> init);

  TVM_DEFINE_OBJECT_REF_METHODS(SequentialSpan, Span, SequentialSpanNode);
};
```

`SequentialSpan` 类继承自 `Span` 类。该类具有以下成员函数：

- `SequentialSpan(Array<Span> spans)`：一个构造函数，用于创建一个`SequentialSpan`对象。它接受一个`Array<Span>`类型的参数`spans`，表示顺序跨度列表。
- `SequentialSpan(std::initializer_list<Span> init)`：另一个构造函数，用于创建一个`SequentialSpan`对象。它接受一个`std::initializer_list<Span>`类型的参数`init`，表示顺序跨度列表。
- `TVM_DEFINE_OBJECT_REF_METHODS(SequentialSpan, Span, SequentialSpanNode)`：一个宏定义，用于定义`SequentialSpan`对象的引用方法。

总体来说，这段代码定义了一个用于表示顺序跨度列表的类，并提供了相应的构造函数和引用方法。